In [2]:
from config import *
from utils import *
from models import *
from train import *
from inference import *
import pickle
import matplotlib.pyplot as plt

[nltk_data] Error loading punkt: <urlopen error [SSL:
[nltk_data]     CERTIFICATE_VERIFY_FAILED] certificate verify failed:
[nltk_data]     unable to get local issuer certificate (_ssl.c:1002)>


## 1. Data Preprocessing

In [3]:
print(device)

cpu


In [5]:
import nltk
import ssl

try:
    _create_unverified_https_context = ssl._create_unverified_context
except AttributeError:
    pass
else:
    ssl._create_default_https_context = _create_unverified_https_context

nltk.download('punkt')


[nltk_data] Downloading package punkt to
[nltk_data]     /Users/ashmitaphuyal/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [6]:
from datasets import load_dataset

def process_text(text):
    # Tokenize the text into sentences
    sentences = nltk.tokenize.sent_tokenize(text)
    # Prepare to collect pairs
    pairs = []
    # Iterate through the sentences and pair them, ensuring no internal tabs
    for i in range(1, len(sentences)):
        # Replace internal tabs in each sentence to avoid confusion in the output format
        sentence1 = sentences[i-1].replace('\t', ' ')
        sentence2 = sentences[i].replace('\t', ' ')
        pair = f"{sentence1}\t{sentence2}"
        pairs.append(pair)
    return pairs

def load_huggingface_data(dataset):
   
    # File to save the pairs
    with open('output_pairs.txt', 'w') as file:
        # Process each text entry in the dataset
        for text in dataset['text']:
            # Get pairs from the current text
            pairs = process_text(text)
            # Write each pair to the file
            for pair in pairs:
                file.write(pair + '\n')

dataset = load_dataset("Amirkid/MedQuad-dataset", split='train')
load_huggingface_data(dataset)

In [7]:
dataset

Dataset({
    features: ['text'],
    num_rows: 32800
})

In [8]:
# Define path to new file
datafile = os.path.join(corpus, "output_pairs.txt")

In [9]:
conversation = read_conversation_from_file(datafile)

In [10]:
len(conversation)

159770

In [11]:
def max_word_count_in_pairs(conversation):
    max_length = 0  # Initialize the maximum length counter
    for index, (question, answer) in enumerate(conversation, start=1):
        # Calculate word count for the question
        question_length = len(question.split())
        # Calculate word count for the answer
        answer_length = len(answer.split())
        
        # Update the maximum word count if the current question or answer has more words
        if question_length > max_length:
            max_length = question_length
        if answer_length > max_length:
            max_length = answer_length

    return max_length

In [12]:
max_word_count_in_pairs(conversation)

753

In [13]:
for index, (question, answer) in enumerate(conversation, start=1):
    print(f"{index}. {question}")
    print(f"   {answer}")
    if index == 10:
        break

1. Any part of your neck  muscles, bones, joints, tendons, ligaments, or nerves  can cause neck problems.
   Neck pain is very common.

2. Neck pain is very common.
   Pain may also come from your shoulder, jaw, head, or upper arms.

3. Pain may also come from your shoulder, jaw, head, or upper arms.
   Muscle strain or tension often causes neck pain.

4. Muscle strain or tension often causes neck pain.
   The problem is usually overuse, such as from sitting at a computer for too long.

5. The problem is usually overuse, such as from sitting at a computer for too long.
   Sometimes you can strain your neck muscles from sleeping in an awkward position or overdoing it during exercise.

6. Sometimes you can strain your neck muscles from sleeping in an awkward position or overdoing it during exercise.
   Falls or accidents, including car accidents, are another common cause of neck pain.

7. Falls or accidents, including car accidents, are another common cause of neck pain.
   Whiplash, a s

## 2 . Data TOkenization & Batching

In [14]:
print(corpus)
print(corpus_name)
print(datafile)
print(save_dir)
MAX_LENGTH = 100
print(MAX_LENGTH)

data/MedQuad
MedQuad
data/MedQuad/output_pairs.txt
model
100


In [15]:
def loadPrepareData(corpus, corpus_name, datafile, MAX_LENGTH):
    try:
        print("Start preparing training data ...")
        voc, pairs = readVocs(datafile, corpus_name)
        print("Read {!s} sentence pairs".format(len(pairs)))
        pairs = filterPairs(pairs, MAX_LENGTH)
        print("Trimmed to {!s} sentence pairs".format(len(pairs)))
        print("Counting words...")
        for pair in pairs:
            voc.addSentence(pair[0])
            voc.addSentence(pair[1])
        print("Counted words:", voc.num_words)
        return voc, pairs
    except Exception as e:
        print(f"An error occurred: {e}")
        return None, None

voc, pairs = loadPrepareData(corpus, corpus_name, datafile, MAX_LENGTH)

Start preparing training data ...
Reading lines...
Read 159770 sentence pairs
Trimmed to 158235 sentence pairs
Counting words...
Counted words: 29126


In [16]:
print(voc.word2index.get('to', UNK_token))
print(pairs[0])

72
['any part of your neck muscles bones joints tendons ligaments or nerves can cause neck problems .', 'neck pain is very common .']


In [17]:
voc_filename = os.path.join( save_dir,'voc.pkl' ) # Name of the file to save the Voc object

# Save the Voc object to a file
with open(voc_filename, 'wb') as voc_file:
    pickle.dump(voc, voc_file)

print(f"Vocabulary object saved to {voc_filename}")

Vocabulary object saved to model/voc.pkl


In [18]:
# Trim voc and pairs
pairs = trimRareWords(voc, pairs, MIN_COUNT)

Trimmed from 158235 pairs to 158235, 1.0000 of total


In [19]:
training_pairs, validation_pairs, testing_pairs = split_data(pairs, train_percent=0.90, validation_percent=0.05, test_percent=0.05)
print(f"Training Pairs: {len(training_pairs)}")
print(f"Validation Pairs: {len(validation_pairs)}")
print(f"Testing Pairs: {len(testing_pairs)}")

Training Pairs: 142411
Validation Pairs: 7911
Testing Pairs: 7913


## 3.  Modeling

In [20]:
# Initialize models and optimizers
embedding = nn.Embedding(voc.num_words, hidden_size).to(device)
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout).to(device)
decoder = LuongAttnDecoderRNN(attn_model, embedding, hidden_size, voc.num_words, decoder_n_layers, dropout).to(device)

In [21]:
# Initialize optimizers after models are assigned to device
encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate_en)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate_de)

if loadFilename:
    checkpoint = torch.load(loadFilename, map_location=device)
    encoder.load_state_dict(checkpoint['en'])
    decoder.load_state_dict(checkpoint['de'])
    encoder_optimizer.load_state_dict(checkpoint['en_opt'])
    decoder_optimizer.load_state_dict(checkpoint['de_opt'])
    embedding.load_state_dict(checkpoint['embedding'])
    voc.__dict__ = checkpoint['voc_dict']

## 4. Training

In [22]:
# Function to load the checkpoint
def load_checkpoint(filepath):
    checkpoint = torch.load(filepath, map_location=torch.device('cpu'))
    return checkpoint

# Load the best model
checkpoint_path = os.path.join(save_dir, model_name, corpus_name, f'best_model_val_per.tar')
checkpoint = load_checkpoint(checkpoint_path)
# print(checkpoint)

#Load Tokenizer
voc1 = Voc(corpus_name)
voc1.__dict__ = checkpoint['voc_dict']

embedding = nn.Embedding(voc1.num_words, hidden_size)
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout)
decoder = LuongAttnDecoderRNN(attn_model, embedding, hidden_size, voc1.num_words, decoder_n_layers, dropout)
encoder.load_state_dict(checkpoint['en'])
decoder.load_state_dict(checkpoint['de'])

# Move models to the appropriate device
encoder = encoder.to(device)
decoder = decoder.to(device)

# Ensure models are in evaluation mode
encoder.eval()
decoder.eval()

LuongAttnDecoderRNN(
  (embedding): Embedding(29126, 512)
  (embedding_dropout): Dropout(p=0.1, inplace=False)
  (gru): GRU(512, 512, num_layers=2, dropout=0.1)
  (concat): Linear(in_features=1024, out_features=512, bias=True)
  (out): Linear(in_features=512, out_features=29126, bias=True)
  (attn): Attn()
)

## 5. Evaluation 

In [24]:
from rouge_score import rouge_scorer

def calculate_rouge_score(reference, candidate):
    scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    scores = scorer.score(reference, candidate)
    rouge_score = (scores['rouge1'].fmeasure + scores['rouge2'].fmeasure + scores['rougeL'].fmeasure) / 3
    return rouge_score

def calculate_precision_recall_f1(reference, candidate):
    true_positives = len(set(reference) & set(candidate))
    precision = true_positives / len(candidate) if len(candidate) > 0 else 0
    recall = true_positives / len(reference) if len(reference) > 0 else 0
    f1_score = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0
    return precision, recall, f1_score

# Assuming 'conversation' is defined and 'searcher', 'voc' are properly initialized
eval_conversations = testing_pairs  

total_bleu_score = 0
total_rouge_score = 0
total_precision = 0
total_recall = 0
total_f1_score = 0

for i, (question, actual_answer) in enumerate(eval_conversations, start=1):
    generated_response = evaluate(encoder, decoder, question, voc, PAD_token, SOS_token, UNK_token, EOS_token, device, max_length=100)
    
    # Calculate BLEU score
    bleu_score = calculate_bleu_score([actual_answer], generated_response)
    total_bleu_score += bleu_score
    
    # Calculate ROUGE score
    reference_corpus = " ".join(actual_answer)  # Flatten the nested list into a single string
    candidate_corpus = " ".join(generated_response)  # Flatten the nested list into a single string
    rouge_score = calculate_rouge_score(reference_corpus, candidate_corpus)
    total_rouge_score += rouge_score
    
    # Calculate precision, recall, and F1 score
    precision, recall, f1_score = calculate_precision_recall_f1(reference_corpus.split(), candidate_corpus.split())
    total_precision += precision
    total_recall += recall
    total_f1_score += f1_score
    
    print(f"----------------------------------------------------------------------------------------------------\n")
    print(f"Q: {question}")
    print(f"Actual Ans: {actual_answer}")
    print(f"Generated Ans: {generated_response}")
    print(f"BLEU Score: {bleu_score}")
    print(f"ROUGE Score: {rouge_score}")
    print(f"Precision: {precision}, Recall: {recall}, F1 Score: {f1_score}\n")

# Calculate averages
average_bleu_score = total_bleu_score / len(eval_conversations)
average_rouge_score = total_rouge_score / len(eval_conversations)
average_precision = total_precision / len(eval_conversations)
average_recall = total_recall / len(eval_conversations)
average_f1_score = total_f1_score / len(eval_conversations)

print(f"Average BLEU Score over {len(eval_conversations)} conversations: {average_bleu_score}")
print(f"Average ROUGE Score over {len(eval_conversations)} conversations: {average_rouge_score}")
print(f"Average Precision over {len(eval_conversations)} conversations: {average_precision}")
print(f"Average Recall over {len(eval_conversations)} conversations: {average_recall}")
print(f"Average F1 Score over {len(eval_conversations)} conversations: {average_f1_score}")


----------------------------------------------------------------------------------------------------

Q: if cancer is in the subglottis treatment may include the following radiation therapy with or without surgery .
Actual Ans: surgery alone .
Generated Ans: the chemotherapy is the the the the the the . . .
BLEU Score: 9.788429383461836e-232
ROUGE Score: 0.17084318360914105
Precision: 0.18421052631578946, Recall: 0.5384615384615384, F1 Score: 0.2745098039215686

----------------------------------------------------------------------------------------------------

Q: ct scan cat scan a procedure that makes a series of detailed pictures of areas inside the body such as the chest or lymph nodes taken from different angles .
Actual Ans: the pictures are made by a computer linked to an xray machine .
Generated Ans: the pictures of a computer linked to a machine
BLEU Score: 0.2365275810472867
ROUGE Score: 0.8012684989429175
Precision: 0.42105263157894735, Recall: 0.3137254901960784, F1 Score:

In [25]:
import torch

def tensor_from_sentence(voc, sentence, device, UNK_token, EOS_token):
    indexes = [voc.word2index[word] if word in voc.word2index else UNK_token for word in sentence.split()]
    indexes.append(EOS_token)
    
    # Get the length of the tensor
    lengths = torch.tensor([len(indexes)], dtype=torch.long, device=device)
    
    # Convert indexes list to tensor
    tensor = torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)
    
    return tensor, lengths

def evaluate(encoder, decoder, question, voc, PAD_token, SOS_token, UNK_token, EOS_token, device, max_length=100):
    # Preprocess the input question
    processed_question = process_text(question)
    
    # Convert the processed question to a tensor
    input_tensor, input_lengths = tensor_from_sentence(voc, processed_question, device)
    
    # Initialize the decoder input with SOS_token
    decoder_input = torch.tensor([[SOS_token]], device=device)
    
    # Initialize the decoder hidden state with encoder's output
    encoder_outputs, encoder_hidden = encoder(input_tensor, input_lengths)
    decoder_hidden = encoder_hidden[:decoder.n_layers]
    
    # Initialize an empty list to store the generated response
    generated_response = []
    
    # Start generating response tokens
    for _ in range(max_length):
        # Generate a single token
        decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
        _, top_index = decoder_output.topk(1)
        generated_token = top_index.squeeze().detach().item()
        
        # Terminate if EOS_token is generated
        if generated_token == EOS_token:
            break
        
        # Append the generated token to the response
        generated_response.append(generated_token)
        
        # Prepare the input for the next iteration
        decoder_input = torch.tensor([[generated_token]], device=device)
    
    # Convert the generated response tokens to words
    generated_response = [voc.index2word[token] for token in generated_response]
    
    # Join the words to form the final response
    generated_response = ' '.join(generated_response)
    
    return generated_response
